# Comparing Toronto and New York Neighborhoods

In [1]:
#Import Libraries
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json 
# converts an address into latitude and longitude 
from geopy.geocoders import Nominatim 
import requests 
 # Converts JSON file into a pandas dataframe
from pandas.io.json import json_normalize


# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
from matplotlib import pyplot as plt

#For cluster analysis 
from sklearn.cluster import KMeans

!pip install folium
import folium 

from IPython.display import HTML
import time

# Import and Clean the Data

In [2]:
#Obtain Postal Code, Borough, and Neighborhood information from Wikipedia
table = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M', header = 0)

#Obtain the first table
df_toronto = table[0]
df_toronto.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [3]:
df_toronto.rename(columns = {"Postcode": "PostalCode", "Neighbourhood": "Neighborhood"}, inplace = True)

#Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned.
df_toronto.drop(df_toronto[df_toronto.Borough == 'Not assigned'].index, inplace=True)
#df.head()

#Combine the neighborhoods that exists in one postal code
df_toronto = df_toronto.groupby(['PostalCode', 'Borough'])['Neighborhood'].apply(lambda x: ','.join(x)).reset_index()
#df.head()

#Change unassigned Neighborhood to its Borough's name
df_toronto.loc[85,'Neighborhood'] = 'Queen\'s Park'

print (df_toronto.shape)

df_toronto.tail()

(103, 3)


PostalCode    Borough                                       Neighborhood
98         M9N       York                                             Weston
99         M9P  Etobicoke                                          Westmount
100        M9R  Etobicoke  Kingsview Village,Martin Grove Gardens,Richvie...
101        M9V  Etobicoke  Albion Gardens,Beaumond Heights,Humbergate,Jam...
102        M9W  Etobicoke                                          Northwest

In [4]:
#Create a dataframe of the latitude and longitudes of the Toronto Neighborhoods
latlong = pd.read_csv("http://cocl.us/Geospatial_data")
latlong.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [5]:
latlong.rename(columns = {"Postal Code": "PostalCode"}, inplace = True)
latlong.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [6]:
latlong.tail()

PostalCode   Latitude  Longitude
98         M9N  43.706876 -79.518188
99         M9P  43.696319 -79.532242
100        M9R  43.688905 -79.554724
101        M9V  43.739416 -79.588437
102        M9W  43.706748 -79.594054

In [7]:
#Join the two tables
df_toronto.set_index("PostalCode")
latlong.set_index("PostalCode")
toronto_neighbor=pd.merge(df_toronto, latlong)
toronto_neighbor.tail()

PostalCode    Borough                                       Neighborhood  \
98         M9N       York                                             Weston   
99         M9P  Etobicoke                                          Westmount   
100        M9R  Etobicoke  Kingsview Village,Martin Grove Gardens,Richvie...   
101        M9V  Etobicoke  Albion Gardens,Beaumond Heights,Humbergate,Jam...   
102        M9W  Etobicoke                                          Northwest   

      Latitude  Longitude  
98   43.706876 -79.518188  
99   43.696319 -79.532242  
100  43.688905 -79.554724  
101  43.739416 -79.588437  
102  43.706748 -79.594054

In [8]:
print('Toronto has {} boroughs and {} neighborhoods.'.format(
        len(toronto_neighbor['Borough'].unique()),
        toronto_neighbor.shape[0]
    )
)

Toronto has 11 boroughs and 103 neighborhoods.


In [9]:
#Next we will add the City to the Neighborhood to be able to identify it later from our New York List
toronto_neighbor['Neighborhood']=toronto_neighbor['Neighborhood'].add(', Toronto')
toronto_neighbor.head()

PostalCode      Borough                                   Neighborhood  \
0        M1B  Scarborough                         Rouge,Malvern, Toronto   
1        M1C  Scarborough  Highland Creek,Rouge Hill,Port Union, Toronto   
2        M1E  Scarborough       Guildwood,Morningside,West Hill, Toronto   
3        M1G  Scarborough                                Woburn, Toronto   
4        M1H  Scarborough                             Cedarbrae, Toronto   

    Latitude  Longitude  
0  43.806686 -79.194353  
1  43.784535 -79.160497  
2  43.763573 -79.188711  
3  43.770992 -79.216917  
4  43.773136 -79.239476

In [10]:
address = 'Toronto, CA'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto, Canada are {}, {}.'.format(latitude, longitude))

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


The geograpical coordinate of Toronto, Canada are 43.653963, -79.387207.


In [11]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_neighbor['Latitude'], toronto_neighbor['Longitude'], toronto_neighbor['Borough'], toronto_neighbor['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='Purple',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

# Utilize the Foursquare API and create a function to generate a litst of nearby Venues

In [12]:
#Exploring with API
{
    "tags": [
        "hide_input",
    ]
}

CLIENT_ID = '1TQX3BIGE0AVURRWD1YKVRLYVZZA5A3MQ52OZOEDFZBKVMJW' # your Foursquare ID
CLIENT_SECRET = 'E513XDA24031SHHX4EBAU4G2PY0CUYXAASQZKNHNZ4LRX1XQ' # your Foursquare Secret
VERSION = '20200217' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1TQX3BIGE0AVURRWD1YKVRLYVZZA5A3MQ52OZOEDFZBKVMJW
CLIENT_SECRET:E513XDA24031SHHX4EBAU4G2PY0CUYXAASQZKNHNZ4LRX1XQ


In [13]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        #print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            100)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    print('Found {} venues in {} neighborhoods.'.format(nearby_venues.shape[0], len(venues_list)))
    
    return(nearby_venues)

In [14]:
toronto_neighbor = getNearbyVenues(names=toronto_neighbor['Neighborhood'],
                                   latitudes=toronto_neighbor['Latitude'],
                                   longitudes=toronto_neighbor['Longitude'],
                                  )

Found 2236 venues in 103 neighborhoods.


In [15]:
#Remove duplicate neighborhoods
toronto_neighbor = toronto_neighbor.drop_duplicates('Neighborhood', keep='first')

In [16]:
print(toronto_neighbor.shape)
toronto_neighbor.head()

(100, 7)


Neighborhood  Neighborhood Latitude  \
0                          Rouge,Malvern, Toronto              43.806686   
2   Highland Creek,Rouge Hill,Port Union, Toronto              43.784535   
4        Guildwood,Morningside,West Hill, Toronto              43.763573   
12                                Woburn, Toronto              43.770992   
15                             Cedarbrae, Toronto              43.773136   

    Neighborhood Longitude                            Venue  Venue Latitude  \
0               -79.194353                          Wendy's       43.807448   
2               -79.160497            Royal Canadian Legion       43.782533   
4               -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   
12              -79.216917                        Starbucks       43.770037   
15              -79.239476         Drupati's Roti & Doubles       43.775222   

    Venue Longitude        Venue Category  
0        -79.199056  Fast Food Restaurant  
2        -79.163085                   Bar  
4        -79.189914           Pizza Place  
12       -79.221156           Coffee Shop  
15       -79.241678  Caribbean Restaurant

In [18]:
#Venues per Neighborhood
toronto_neighbor.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide,King,Richmond, Toronto                                         1   
Agincourt North,L'Amoreaux East,Milliken,Steele...                      1   
Agincourt, Toronto                                                      1   
Albion Gardens,Beaumond Heights,Humbergate,Jame...                      1   
Alderwood,Long Branch, Toronto                                          1   
Bathurst Manor,Downsview North,Wilson Heights, ...                      1   
Bayview Village, Toronto                                                1   
Bedford Park,Lawrence Manor East, Toronto                               1   
Berczy Park, Toronto                                                    1   
Birch Cliff,Cliffside West, Toronto                                     1   
Bloordale Gardens,Eringate,Markland Wood,Old Bu...                      1   
Brockton,Exhibition Place,Parkdale Village, Tor...                      1   
Business Reply Mail Processing Centre 969 Easte...                      1   
CFB Toronto,Downsview East, Toronto                                     1   
CN Tower,Bathurst Quay,Island airport,Harbourfr...                      1   
Cabbagetown,St. James Town, Toronto                                     1   
Caledonia-Fairbanks, Toronto                                            1   
Canada Post Gateway Processing Centre, Toronto                          1   
Cedarbrae, Toronto                                                      1   
Central Bay Street, Toronto                                             1   
Chinatown,Grange Park,Kensington Market, Toronto                        1   
Christie, Toronto                                                       1   
Church and Wellesley, Toronto                                           1   
Clairlea,Golden Mile,Oakridge, Toronto                                  1   
Clarks Corners,Sullivan,Tam O'Shanter, Toronto                          1   
Cliffcrest,Cliffside,Scarborough Village West, ...                      1   
Cloverdale,Islington,Martin Grove,Princess Gard...                      1   
Commerce Court,Victoria Hotel, Toronto                                  1   
Davisville North, Toronto                                               1   
Davisville, Toronto                                                     1   
Deer Park,Forest Hill SE,Rathnelly,South Hill,S...                      1   
Del Ray,Keelesdale,Mount Dennis,Silverthorn, To...                      1   
Design Exchange,Toronto Dominion Centre, Toronto                        1   
Don Mills North, Toronto                                                1   
Dorset Park,Scarborough Town Centre,Wexford Hei...                      1   
Dovercourt Village,Dufferin, Toronto                                    1   
Downsview Central, Toronto                                              1   
Downsview Northwest, Toronto                                            1   
Downsview West, Toronto                                                 1   
Downsview,North Park,Upwood Park, Toronto                               1   
East Birchmount Park,Ionview,Kennedy Park, Toronto                      1   
East Toronto, Toronto                                                   1   
Emery,Humberlea, Toronto                                                1   
Fairview,Henry Farm,Oriole, Toronto                                     1   
First Canadian Place,Underground city, Toronto                          1   
Flemingdon Park,Don Mills South, Toronto                                1   
Forest Hill North,Forest Hill West, Toronto                             1   
Glencairn, Toronto                                                      1   
Guildwood,Morningside,West Hill, Toronto                                1   
Harbord,University of Toronto, Toronto                                  1   
Harbourfront East,Toronto Islands,Union Station.

In [19]:
print('There are {} distinct venues in {} categories.'.format(
    len(toronto_neighbor['Venue'].unique()),len(toronto_neighbor['Venue Category'].unique())))

#print('There are {} uniques categories.'.format(len(scarborough_venues['Venue Category'].unique())))

There are 93 distinct venues in 58 categories.


In [20]:
#analyzing the neighborhood

# one hot encoding
toronto_onehot = pd.get_dummies(toronto_neighbor[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_neighbor['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Airport  Arts & Crafts Store  Bakery  Bank  Bar  \
0             0        0                    0       0     0    0   
2             0        0                    0       0     0    1   
4             0        0                    0       0     0    0   
12            0        0                    0       0     0    0   
15            0        0                    0       0     0    0   

    Baseball Field  Boutique  Breakfast Spot  Brewery  Cafeteria  Café  \
0                0         0               0        0          0     0   
2                0         0               0        0          0     0   
4                0         0               0        0          0     0   
12               0         0               0        0          0     0   
15               0         0               0        0          0     0   

    Caribbean Restaurant  Chinese Restaurant  Clothing Store  Coffee Shop  \
0                      0                   0               0            0   
2                      0                   0               0            0   
4                      0                   0               0            0   
12                     0                   0               0            1   
15                     1                   0               0            0   

    Concert Hall  Convenience Store  Deli / Bodega  Department Store  \
0              0                  0              0                 0   
2              0                  0              0                 0   
4              0                  0              0                 0   
12             0                  0              0                 0   
15             0                  0              0                 0   

    Dessert Shop  Dog Run  Fast Food Restaurant  Field  Food  Garden  \
0              0        0                     1      0     0       0   
2              0        0                     0      0     0       0   
4              0        0                     0      0     0       0   
12             0        0                     0      0     0       0   
15             0        0                     0      0     0       0   

    Gastropub  Golf Course  Greek Restaurant  Grocery Store  Gym  \
0           0            0                 0              0    0   
2           0            0                 0              0    0   
4           0            0                 0              0    0   
12          0            0                 0              0    0   
15          0            0                 0              0    0   

    Gym / Fitness Center  Hockey Arena  Home Service  Hotel  Ice Cream Shop  \
0                      0             0             0      0               0   
2                      0             0             0      0               0   
4                      0             0             0      0               0   
12                     0             0             0      0               0   
15                     0             0             0      0               0   

    Indian Restaurant  Italian Restaurant  Japanese Restaurant  Liquor Store  \
0                   0                   0                    0             0   
2                   0                   0                    0             0   
4                   0                   0                    0             0   
12                  0                   0                    0             0   
15                  0                   0                    0             0   

    Massage Studio  Motel  Museum  \
0                0      0       0   
2                0      0       0   
4                0      0       0   
12               0      0       0   
15               0      0       0   

                                     Neighborhood  Park  Pizza Place  \
0                          Rouge,Malvern, Toronto     0            0   
2   Highland Creek,Rouge Hill,Port Union, Toronto     0            0   
4        Guildwoo

In [21]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  Airport  \
0                     Adelaide,King,Richmond, Toronto            0        0   
1   Agincourt North,L'Amoreaux East,Milliken,Steel...            0        0   
2                                  Agincourt, Toronto            0        0   
3   Albion Gardens,Beaumond Heights,Humbergate,Jam...            0        0   
4                      Alderwood,Long Branch, Toronto            0        0   
5   Bathurst Manor,Downsview North,Wilson Heights,...            0        0   
6                            Bayview Village, Toronto            0        0   
7           Bedford Park,Lawrence Manor East, Toronto            0        0   
8                                Berczy Park, Toronto            0        0   
9                 Birch Cliff,Cliffside West, Toronto            0        0   
10  Bloordale Gardens,Eringate,Markland Wood,Old B...            0        0   
11  Brockton,Exhibition Place,Parkdale Village, To...            0        0   
12  Business Reply Mail Processing Centre 969 East...            0        0   
13                CFB Toronto,Downsview East, Toronto            0        1   
14  CN Tower,Bathurst Quay,Island airport,Harbourf...            0        1   
15                Cabbagetown,St. James Town, Toronto            0        0   
16                       Caledonia-Fairbanks, Toronto            0        0   
17     Canada Post Gateway Processing Centre, Toronto            0        0   
18                                 Cedarbrae, Toronto            0        0   
19                        Central Bay Street, Toronto            0        0   
20   Chinatown,Grange Park,Kensington Market, Toronto            0        0   
21                                  Christie, Toronto            0        0   
22                      Church and Wellesley, Toronto            0        0   
23             Clairlea,Golden Mile,Oakridge, Toronto            0        0   
24     Clarks Corners,Sullivan,Tam O'Shanter, Toronto            0        0   
25  Cliffcrest,Cliffside,Scarborough Village West,...            0        0   
26  Cloverdale,Islington,Martin Grove,Princess Gar...            0        0   
27             Commerce Court,Victoria Hotel, Toronto            0        0   
28                          Davisville North, Toronto            0        0   
29                                Davisville, Toronto            0        0   
30  Deer Park,Forest Hill SE,Rathnelly,South Hill,...            0        0   
31  Del Ray,Keelesdale,Mount Dennis,Silverthorn, T...            0        0   
32   Design Exchange,Toronto Dominion Centre, Toronto            0        0   
33                           Don Mills North, Toronto            0        0   
34  Dorset Park,Scarborough Town Centre,Wexford He...            0        0   
35               Dovercourt Village,Dufferin, Toronto            0        0   
36                         Downsview Central, Toronto            0        0   
37                       Downsview Northwest, Toronto            0        0   
38                            Downsview West, Toronto            0        0   
39          Downsview,North Park,Upwood Park, Toronto            0        0   
40  East Birchmount Park,Ionview,Kennedy Park, Tor...            0        0   
41                              East Toronto, Toronto            0        0   
42                           Emery,Humberlea, Toronto            0        0   
43                Fairview,Henry Farm,Oriole, Toronto            0        0   
44     First Canadian Place,Underground city, Toronto            0        0   
45           Flemingdon Park,Don Mills South, Toronto            0        0   
46        Forest Hill North,Forest Hill West, Toronto            0        0   
47                                 Glencairn, Toronto            0        0   
48           Guildwood,Morningside,West Hill, Toronto            0        0   
49             Harbord,University of Toronto, Toronto            0        0   
50  Harbourf

In [22]:
num_top_venues = 10

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond, Toronto----
                  venue  freq
0          Concert Hall   1.0
1           Yoga Studio   0.0
2                Museum   0.0
3  Gym / Fitness Center   0.0
4          Hockey Arena   0.0
5          Home Service   0.0
6                 Hotel   0.0
7        Ice Cream Shop   0.0
8     Indian Restaurant   0.0
9    Italian Restaurant   0.0


----Agincourt North,L'Amoreaux East,Milliken,Steeles East, Toronto----
                  venue  freq
0                  Park   1.0
1         Grocery Store   0.0
2  Gym / Fitness Center   0.0
3          Hockey Arena   0.0
4          Home Service   0.0
5                 Hotel   0.0
6        Ice Cream Shop   0.0
7     Indian Restaurant   0.0
8    Italian Restaurant   0.0
9   Japanese Restaurant   0.0


----Agincourt, Toronto----
                  venue  freq
0        Breakfast Spot   1.0
1           Yoga Studio   0.0
2                  Park   0.0
3  Gym / Fitness Center   0.0
4          Hockey Arena   0.0
5          Home Se

In [23]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

# List of Nearby Venues for each Toronto Neighborhood

In [24]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
t_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
t_neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    t_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

t_neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue  \
0                     Adelaide,King,Richmond, Toronto          Concert Hall   
1   Agincourt North,L'Amoreaux East,Milliken,Steel...                  Park   
2                                  Agincourt, Toronto        Breakfast Spot   
3   Albion Gardens,Beaumond Heights,Humbergate,Jam...        Sandwich Place   
4                      Alderwood,Long Branch, Toronto           Pizza Place   
5   Bathurst Manor,Downsview North,Wilson Heights,...         Deli / Bodega   
6                            Bayview Village, Toronto    Chinese Restaurant   
7           Bedford Park,Lawrence Manor East, Toronto                  Café   
8                                Berczy Park, Toronto            Steakhouse   
9                 Birch Cliff,Cliffside West, Toronto                  Café   
10  Bloordale Gardens,Eringate,Markland Wood,Old B...          Liquor Store   
11  Brockton,Exhibition Place,Parkdale Village, To...                   Gym   
12  Business Reply Mail Processing Centre 969 East...               Brewery   
13                CFB Toronto,Downsview East, Toronto               Airport   
14  CN Tower,Bathurst Quay,Island airport,Harbourf...               Airport   
15                Cabbagetown,St. James Town, Toronto     Indian Restaurant   
16                       Caledonia-Fairbanks, Toronto                  Park   
17     Canada Post Gateway Processing Centre, Toronto                 Hotel   
18                                 Cedarbrae, Toronto  Caribbean Restaurant   
19                        Central Bay Street, Toronto           Coffee Shop   
20   Chinatown,Grange Park,Kensington Market, Toronto   Arts & Crafts Store   
21                                  Christie, Toronto         Grocery Store   
22                      Church and Wellesley, Toronto      Theme Restaurant   
23             Clairlea,Golden Mile,Oakridge, Toronto        Ice Cream Shop   
24     Clarks Corners,Sullivan,Tam O'Shanter, Toronto    Italian Restaurant   
25  Cliffcrest,Cliffside,Scarborough Village West,...                 Motel   
26  Cloverdale,Islington,Martin Grove,Princess Gar...          Home Service   
27             Commerce Court,Victoria Hotel, Toronto                   Gym   
28                          Davisville North, Toronto                  Park   
29                                Davisville, Toronto          Dessert Shop   
30  Deer Park,Forest Hill SE,Rathnelly,South Hill,...          Liquor Store   
31  Del Ray,Keelesdale,Mount Dennis,Silverthorn, T...        Sandwich Place   
32   Design Exchange,Toronto Dominion Centre, Toronto                   Gym   
33                           Don Mills North, Toronto  Gym / Fitness Center   
34  Dorset Park,Scarborough Town Centre,Wexford He...     Indian Restaurant   
35               Dovercourt Village,Dufferin, Toronto                   Bar   
36                         Downsview Central, Toronto        Baseball Field   
37                       Downsview Northwest, Toronto         Grocery Store   
38                            Downsview West, Toronto                  Bank   
39          Downsview,North Park,Upwood Park, Toronto                Bakery   
40  East Birchmount Park,Ionview,Kennedy Park, Tor...      Department Store   
41                              East Toronto, Toronto                  Park   
42                           Emery,Humberlea, Toronto        Baseball Field   
43                Fairview,Henry Farm,Oriole, Toronto      Toy / Game Store   
44     First Canadian Place,Underground city, Toronto                   Gym   
45           Flemingdon Park,Don Mills South, Toronto                   Gym   
46        Forest Hill North,Forest Hill West, Toronto                 Trail   
47                                 Glencairn, Toronto                Bakery   
48           Guildwood,Morningside,West Hill, Toronto           Pizza Place   
49             Harbord,University of Toronto, Toronto   Japanese Restaurant   
50  Harbourf

In [25]:
t_neighborhoods_venues_sorted.iloc[11,]

Neighborhood              Brockton,Exhibition Place,Parkdale Village, To...
1st Most Common Venue                                                   Gym
2nd Most Common Venue                                           Wings Joint
3rd Most Common Venue                                        Clothing Store
4th Most Common Venue                                                Garden
5th Most Common Venue                                                  Food
6th Most Common Venue                                                 Field
7th Most Common Venue                                  Fast Food Restaurant
8th Most Common Venue                                               Dog Run
9th Most Common Venue                                          Dessert Shop
10th Most Common Venue                                     Department Store
Name: 11, dtype: object

# Pre-Process the New York Data before Clustering together with the Toronto Data 

In [26]:
# New York Data

!wget -q -O 'newyork_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print('Data downloaded!')

Data downloaded!


In [27]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [28]:
ny_neighborhoods_data = newyork_data['features']

In [29]:
ny_neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [30]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
ny_neighborhoods = pd.DataFrame(columns=column_names)

In [31]:
for data in ny_neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    ny_neighborhoods = ny_neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [32]:
ny_neighborhoods.tail()

Borough  Neighborhood   Latitude  Longitude
301      Manhattan  Hudson Yards  40.756658 -74.000111
302         Queens       Hammels  40.587338 -73.805530
303         Queens     Bayswater  40.611322 -73.765968
304         Queens  Queensbridge  40.756091 -73.945631
305  Staten Island     Fox Hills  40.617311 -74.081740

In [33]:
#Next we will add the City to the Neighborhood to be able to identify it later from our New York List
ny_neighborhoods['Neighborhood']=ny_neighborhoods['Neighborhood'].add(', New York')
ny_neighborhoods.head()

Borough           Neighborhood   Latitude  Longitude
0   Bronx    Wakefield, New York  40.894705 -73.847201
1   Bronx   Co-op City, New York  40.874294 -73.829939
2   Bronx  Eastchester, New York  40.887556 -73.827806
3   Bronx    Fieldston, New York  40.895437 -73.905643
4   Bronx    Riverdale, New York  40.890834 -73.912585

In [34]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(ny_neighborhoods['Borough'].unique()),
        ny_neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [35]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent = 'my-application')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [36]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(ny_neighborhoods['Latitude'], ny_neighborhoods['Longitude'], ny_neighborhoods['Borough'], ny_neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [37]:
neighborhood_lat = ny_neighborhoods.loc[10, 'Latitude'] # neighborhood latitude value
neighborhood_lon = ny_neighborhoods.loc[10, 'Longitude'] # neighborhood longitude value

neighborhood_name = ny_neighborhoods.loc[10, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_lat, 
                                                               neighborhood_lon))

Latitude and longitude values of Baychester, New York are 40.866858107252696, -73.83579759808117.


# Utilize the Foursquare API and create a function to generate a litst of nearby Venues

In [39]:
# type your answer here
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_lat, 
    neighborhood_lon, 
    radius, 
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=1TQX3BIGE0AVURRWD1YKVRLYVZZA5A3MQ52OZOEDFZBKVMJW&client_secret=E513XDA24031SHHX4EBAU4G2PY0CUYXAASQZKNHNZ4LRX1XQ&v=20200217&ll=40.866858107252696,-73.83579759808117&radius=500&limit=100'

In [40]:
#Send the GET request
results = requests.get(url).json()

In [41]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [42]:
venues = results['response']['groups'][0]['items']
    
ny_nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
ny_nearby_venues =ny_nearby_venues.loc[:, filtered_columns]

# filter the category for each row
ny_nearby_venues['venue.categories'] = ny_nearby_venues.apply(get_category_type, axis=1)

# clean columns
ny_nearby_venues.columns = [col.split(".")[-1] for col in ny_nearby_venues.columns]

ny_nearby_venues.head()

name            categories        lat        lng
0   Caridad & Louie    Spanish Restaurant  40.865843 -73.837707
1           Dunkin'            Donut Shop  40.867800 -73.833365
2    Planet Fitness  Gym / Fitness Center  40.863298 -73.835568
3        Chase Bank                  Bank  40.866132 -73.838398
4  ALDI Food Market           Supermarket  40.863250 -73.835002

In [44]:
#Function 'getNearbyVenues' was defined earlier
ny_venues = getNearbyVenues(names=ny_neighborhoods['Neighborhood'],
                                   latitudes=ny_neighborhoods['Latitude'],
                                   longitudes=ny_neighborhoods['Longitude'])

Found 10287 venues in 306 neighborhoods.


In [45]:
ny_venues = ny_venues.drop_duplicates('Neighborhood', keep='first')

In [46]:
ny_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Wakefield, New York              40.894705              -73.847201   
10   Co-op City, New York              40.874294              -73.829939   
26  Eastchester, New York              40.887556              -73.827806   
45    Fieldston, New York              40.895437              -73.905643   
49    Riverdale, New York              40.890834              -73.912585   

                    Venue  Venue Latitude  Venue Longitude  \
0        Lollipops Gelato       40.894123       -73.845892   
10            Dollar Tree       40.870125       -73.828989   
26            Fish & Ting       40.885656       -73.829197   
45  Fieldston Road Circle       40.894489       -73.905621   
49          Riverdale Ave       40.890425       -73.910248   

          Venue Category  
0           Dessert Shop  
10        Discount Store  
26  Caribbean Restaurant  
45                 Plaza  
49                 Plaza

In [47]:
#Venues per Neighborhood
ny_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                 
Allerton, New York                                       1   
Annadale, New York                                       1   
Arden Heights, New York                                  1   
Arlington, New York                                      1   
Arrochar, New York                                       1   
Arverne, New York                                        1   
Astoria Heights, New York                                1   
Astoria, New York                                        1   
Auburndale, New York                                     1   
Bath Beach, New York                                     1   
Battery Park City, New York                              1   
Bay Ridge, New York                                      1   
Bay Terrace, New York                                    1   
Baychester, New York                                     1   
Bayside, New York                                        1   
Bayswater, New York                                      1   
Bedford Park, New York                                   1   
Bedford Stuyvesant, New York                             1   
Beechhurst, New York                                     1   
Bellaire, New York                                       1   
Belle Harbor, New York                                   1   
Bellerose, New York                                      1   
Belmont, New York                                        1   
Bensonhurst, New York                                    1   
Bergen Beach, New York                                   1   
Blissville, New York                                     1   
Bloomfield, New York                                     1   
Boerum Hill, New York                                    1   
Borough Park, New York                                   1   
Breezy Point, New York                                   1   
Briarwood, New York                                      1   
Brighton Beach, New York                                 1   
Broad Channel, New York                                  1   
Broadway Junction, New York                              1   
Bronxdale, New York                                      1   
Brooklyn Heights, New York                               1   
Brookville, New York                                     1   
Brownsville, New York                                    1   
Bulls Head, New York                                     1   
Bushwick, New York                                       1   
Butler Manor, New York                                   1   
Cambria Heights, New York                                1   
Canarsie, New York                                       1   
Carnegie Hill, New York                                  1   
Carroll Gardens, New York                                1   
Castle Hill, New York                                    1   
Castleton Corners, New York                              1   
Central Harlem, New York                                 1   
Charleston, New York                                     1   
Chelsea, New York                                        1   
Chinatown, New York                                      1   
City Island, New York                                    1   
City Line, New York                                      1   
Civic Center, New York                                   1   
Claremont Village, New York                              1   
Clason Point, New York                                   1   
Clifton, New York                                        1   
Clinton Hill, New York                                   1   
Clinton, New York                                        1   
Co-op City, New York                                     1   
Cobble Hill, New York                                    1   
College Point, New York                                  1   
Concord, New York                                        1   
Concour

In [48]:
# one hot encoding
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = ny_venues['Neighborhood'] 

# move neighborhood column to the first column

neighbor = ny_onehot['Neighborhood']
ny_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)
ny_onehot.insert(0, 'Neighborhood', neighbor)

ny_onehot.head()

Neighborhood  African Restaurant  American Restaurant  Arcade  \
0     Wakefield, New York                   0                    0       0   
10   Co-op City, New York                   0                    0       0   
26  Eastchester, New York                   0                    0       0   
45    Fieldston, New York                   0                    0       0   
49    Riverdale, New York                   0                    0       0   

    Art Gallery  Art Museum  Arts & Crafts Store  BBQ Joint  Bagel Shop  \
0             0           0                    0          0           0   
10            0           0                    0          0           0   
26            0           0                    0          0           0   
45            0           0                    0          0           0   
49            0           0                    0          0           0   

    Bakery  Bar  Baseball Field  Beach  Beer Bar  Beer Store  Bookstore  \
0        0    0               0      0         0           0          0   
10       0    0               0      0         0           0          0   
26       0    0               0      0         0           0          0   
45       0    0               0      0         0           0          0   
49       0    0               0      0         0           0          0   

    Boutique  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0           0                     0               0        0   
10         0           0                     0               0        0   
26         0           0                     0               0        0   
45         0           0                     0               0        0   
49         0           0                     0               0        0   

    Bubble Tea Shop  Burger Joint  Bus Stop  Café  Cajun / Creole Restaurant  \
0                 0             0         0     0                          0   
10                0             0         0     0                          0   
26                0             0         0     0                          0   
45                0             0         0     0                          0   
49                0             0         0     0                          0   

    Caribbean Restaurant  Casino  Cocktail Bar  Coffee Shop  \
0                      0       0             0            0   
10                     0       0             0            0   
26                     1       0             0            0   
45                     0       0             0            0   
49                     0       0             0            0   

    College Basketball Court  Convenience Store  Cosmetics Shop  Cycle Studio  \
0                          0                  0               0             0   
10                         0                  0               0             0   
26                         0                  0               0             0   
45                         0                  0               0             0   
49                         0                  0               0             0   

    Dance Studio  Deli / Bodega  Dessert Shop  Diner  Discount Store  Dog Run  \
0              0              0             1      0               0        0   
10             0              0             0      0               1        0   
26             0              0             0      0               0        0   
45             0              0             0      0               0        0   
49             0              0             0      0               0        0   

    Donut Shop  Dumpling Restaurant  Farm  Food  Food & Drink Shop  \
0            0                    0     0     0                  0   
10           0                    0     0     0                  0   
26           0                    0     0     0                  0   
45           0                    0     0     0                  0   
49     

In [49]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  African Restaurant  \
0                     Allerton, New York                   0   
1                     Annadale, New York                   0   
2                Arden Heights, New York                   0   
3                    Arlington, New York                   0   
4                     Arrochar, New York                   0   
5                      Arverne, New York                   0   
6              Astoria Heights, New York                   0   
7                      Astoria, New York                   0   
8                   Auburndale, New York                   0   
9                   Bath Beach, New York                   0   
10           Battery Park City, New York                   0   
11                   Bay Ridge, New York                   0   
12                 Bay Terrace, New York                   0   
13                  Baychester, New York                   0   
14                     Bayside, New York                   0   
15                   Bayswater, New York                   0   
16                Bedford Park, New York                   0   
17          Bedford Stuyvesant, New York                   0   
18                  Beechhurst, New York                   0   
19                    Bellaire, New York                   0   
20                Belle Harbor, New York                   0   
21                   Bellerose, New York                   0   
22                     Belmont, New York                   0   
23                 Bensonhurst, New York                   0   
24                Bergen Beach, New York                   0   
25                  Blissville, New York                   0   
26                  Bloomfield, New York                   0   
27                 Boerum Hill, New York                   0   
28                Borough Park, New York                   0   
29                Breezy Point, New York                   0   
30                   Briarwood, New York                   0   
31              Brighton Beach, New York                   0   
32               Broad Channel, New York                   0   
33           Broadway Junction, New York                   0   
34                   Bronxdale, New York                   0   
35            Brooklyn Heights, New York                   0   
36                  Brookville, New York                   0   
37                 Brownsville, New York                   0   
38                  Bulls Head, New York                   0   
39                    Bushwick, New York                   0   
40                Butler Manor, New York                   0   
41             Cambria Heights, New York                   0   
42                    Canarsie, New York                   0   
43               Carnegie Hill, New York                   0   
44             Carroll Gardens, New York                   0   
45                 Castle Hill, New York                   0   
46           Castleton Corners, New York                   0   
47              Central Harlem, New York                   0   
48                  Charleston, New York                   0   
49                     Chelsea, New York                   0   
50                   Chinatown, New York                   0   
51                 City Island, New York                   0   
52                   City Line, New York                   0   
53                Civic Center, New York                   0   
54           Claremont Village, New York                   0   
55                Clason Point, New York                   0   
56                     Clifton, New York                   0   
57                Clinton Hill, New York                   0   
58                     Clinton, New York                   0   
59                  Co-op City, New York                   0   
60                 Cobble Hill, New York                   0   
61               College Point, New York                   0

In [50]:
num_top_venues = 5

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton, New York----
                venue  freq
0         Pizza Place   1.0
1  African Restaurant   0.0
2          Nail Salon   0.0
3                Pool   0.0
4   Polish Restaurant   0.0


----Annadale, New York----
                venue  freq
0          Sports Bar   1.0
1  African Restaurant   0.0
2              Museum   0.0
3   Polish Restaurant   0.0
4               Plaza   0.0


----Arden Heights, New York----
                venue  freq
0         Pizza Place   1.0
1  African Restaurant   0.0
2          Nail Salon   0.0
3                Pool   0.0
4   Polish Restaurant   0.0


----Arlington, New York----
                     venue  freq
0                 Bus Stop   1.0
1       African Restaurant   0.0
2  New American Restaurant   0.0
3                     Pool   0.0
4        Polish Restaurant   0.0


----Arrochar, New York----
                venue  freq
0         Pizza Place   1.0
1  African Restaurant   0.0
2          Nail Salon   0.0
3                Pool   0.0
4   Polis

In [51]:
#Function to sort venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

# Generate a list of nearby venues for New York neighborhoods

In [78]:
# Create the new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
ny_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
ny_neighborhoods_venues_sorted['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    ny_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

ny_neighborhoods_venues_sorted

Neighborhood            1st Most Common Venue  \
0                     Allerton, New York                      Pizza Place   
1                     Annadale, New York                       Sports Bar   
2                Arden Heights, New York                      Pizza Place   
3                    Arlington, New York                         Bus Stop   
4                     Arrochar, New York                      Pizza Place   
5                      Arverne, New York                            Beach   
6              Astoria Heights, New York                            Plaza   
7                      Astoria, New York             Brazilian Restaurant   
8                   Auburndale, New York               Italian Restaurant   
9                   Bath Beach, New York                             Park   
10           Battery Park City, New York                             Park   
11                   Bay Ridge, New York                              Spa   
12                 Bay Terrace, New York                           Bakery   
13                  Baychester, New York               Spanish Restaurant   
14                     Bayside, New York                 Greek Restaurant   
15                   Bayswater, New York                       Playground   
16                Bedford Park, New York                             Park   
17          Bedford Stuyvesant, New York                         Boutique   
18                  Beechhurst, New York                    Deli / Bodega   
19                    Bellaire, New York               Italian Restaurant   
20                Belle Harbor, New York                            Beach   
21                   Bellerose, New York                            Diner   
22                     Belmont, New York               Italian Restaurant   
23                 Bensonhurst, New York               Italian Restaurant   
24                Bergen Beach, New York                       Donut Shop   
25                  Blissville, New York                              Bar   
26                  Bloomfield, New York                Recreation Center   
27                 Boerum Hill, New York               Italian Restaurant   
28                Borough Park, New York              American Restaurant   
29                Breezy Point, New York              Monument / Landmark   
30                   Briarwood, New York                      Coffee Shop   
31              Brighton Beach, New York                     Gourmet Shop   
32               Broad Channel, New York              Sporting Goods Shop   
33           Broadway Junction, New York                   Sandwich Place   
34                   Bronxdale, New York                      Pizza Place   
35            Brooklyn Heights, New York                   History Museum   
36                  Brookville, New York                    Deli / Bodega   
37                 Brownsville, New York               Spanish Restaurant   
38                  Bulls Head, New York                 Sushi Restaurant   
39                    Bushwick, New York                Korean Restaurant   
40                Butler Manor, New York                Convenience Store   
41             Cambria Heights, New York                     Liquor Store   
42                    Canarsie, New York             Caribbean Restaurant   
43               Carnegie Hill, New York                        Bookstore   
44             Carroll Gardens, New York                      Coffee Shop   
45                 Castle Hill, New York                           Market   
46           Castleton Corners, New York                      Pizza Place   
47              Central Harlem, New York                     Cycle Studio   
48                  Charleston, New York                        Gift Shop   
49                     Chelsea, New York                         Beer Bar   
50                   Chinatown, New York                   Sandwich Place   
51                 City 

# Next we will combine the NY and Toronto list and cluster them together. 

In [53]:
# Combine toronto_neighbor and ny_venues to create final_group
#Now that we've seen the top venues for NY and Toronto individually, let's create a combined table to cluster like neighborhoods.
frames = [toronto_neighbor, ny_venues]
group_df = pd.concat(frames)
group_df.tail()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
10164  Hudson Yards, New York              40.756658              -74.000111   
10246       Hammels, New York              40.587338              -73.805530   
10264     Bayswater, New York              40.611322              -73.765968   
10266  Queensbridge, New York              40.756091              -73.945631   
10282     Fox Hills, New York              40.617311              -74.081740   

                                          Venue  Venue Latitude  \
10164                          Bella Abzug Park       40.755580   
10246          Far Rockaway Beach - 81st Street       40.586176   
10264                     Westbourne Playground       40.608445   
10266  Queensboro Bridge Pedestrian & Bike Path       40.755201   
10282                                    SUBWAY       40.618939   

       Venue Longitude  Venue Category  
10164       -74.000344            Park  
10246       -73.807452           Beach  
10264       -73.764480      Playground  
10266       -73.950445  Scenic Lookout  
10282       -74.082881  Sandwich Place

In [54]:
# one hot encoding
combo_onehot = pd.get_dummies(group_df[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
combo_onehot['Neighborhood'] = group_df['Neighborhood'] 

# move neighborhood column to the first column

neighbor = combo_onehot['Neighborhood']
combo_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)
combo_onehot.insert(0, 'Neighborhood', neighbor)

combo_onehot.head()

Neighborhood  African Restaurant  \
0                          Rouge,Malvern, Toronto                   0   
2   Highland Creek,Rouge Hill,Port Union, Toronto                   0   
4        Guildwood,Morningside,West Hill, Toronto                   0   
12                                Woburn, Toronto                   0   
15                             Cedarbrae, Toronto                   0   

    Airport  American Restaurant  Arcade  Art Gallery  Art Museum  \
0         0                    0       0            0           0   
2         0                    0       0            0           0   
4         0                    0       0            0           0   
12        0                    0       0            0           0   
15        0                    0       0            0           0   

    Arts & Crafts Store  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                     0          0           0       0     0    0   
2                     0          0           0       0     0    1   
4                     0          0           0       0     0    0   
12                    0          0           0       0     0    0   
15                    0          0           0       0     0    0   

    Baseball Field  Beach  Beer Bar  Beer Store  Bookstore  Boutique  \
0                0      0         0           0          0         0   
2                0      0         0           0          0         0   
4                0      0         0           0          0         0   
12               0      0         0           0          0         0   
15               0      0         0           0          0         0   

    Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0            0                     0               0        0   
2            0                     0               0        0   
4            0                     0               0        0   
12           0                     0               0        0   
15           0                     0               0        0   

    Bubble Tea Shop  Burger Joint  Bus Stop  Cafeteria  Café  \
0                 0             0         0          0     0   
2                 0             0         0          0     0   
4                 0             0         0          0     0   
12                0             0         0          0     0   
15                0             0         0          0     0   

    Cajun / Creole Restaurant  Caribbean Restaurant  Casino  \
0                           0                     0       0   
2                           0                     0       0   
4                           0                     0       0   
12                          0                     0       0   
15                          0                     1       0   

    Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0                    0               0             0            0   
2                    0               0             0            0   
4                    0               0             0            0   
12                   0               0             0            1   
15                   0               0             0            0   

    College Basketball Court  Concert Hall  Convenience Store  Cosmetics Shop  \
0                          0             0                  0               0   
2                          0             0                  0               0   
4                          0             0                  0               0   
12                         0             0                  0               0   
15                         0             0                  0               0   

    Cycle Studio  Dance Studio  Deli / Bodega  Department Store  Dessert Shop  \
0              0             0              0                 0             0   
2              0             0              0                 0             0   
4              0             0     

In [55]:
final_group = combo_onehot.groupby('Neighborhood').mean().reset_index()
final_group.head()

Neighborhood  African Restaurant  \
0                    Adelaide,King,Richmond, Toronto                   0   
1  Agincourt North,L'Amoreaux East,Milliken,Steel...                   0   
2                                 Agincourt, Toronto                   0   
3  Albion Gardens,Beaumond Heights,Humbergate,Jam...                   0   
4                     Alderwood,Long Branch, Toronto                   0   

   Airport  American Restaurant  Arcade  Art Gallery  Art Museum  \
0        0                    0       0            0           0   
1        0                    0       0            0           0   
2        0                    0       0            0           0   
3        0                    0       0            0           0   
4        0                    0       0            0           0   

   Arts & Crafts Store  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                    0          0           0       0     0    0   
1                    0          0           0       0     0    0   
2                    0          0           0       0     0    0   
3                    0          0           0       0     0    0   
4                    0          0           0       0     0    0   

   Baseball Field  Beach  Beer Bar  Beer Store  Bookstore  Boutique  \
0               0      0         0           0          0         0   
1               0      0         0           0          0         0   
2               0      0         0           0          0         0   
3               0      0         0           0          0         0   
4               0      0         0           0          0         0   

   Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  \
0           0                     0               0        0                0   
1           0                     0               0        0                0   
2           0                     0               1        0                0   
3           0                     0               0        0                0   
4           0                     0               0        0                0   

   Burger Joint  Bus Stop  Cafeteria  Café  Cajun / Creole Restaurant  \
0             0         0          0     0                          0   
1             0         0          0     0                          0   
2             0         0          0     0                          0   
3             0         0          0     0                          0   
4             0         0          0     0                          0   

   Caribbean Restaurant  Casino  Chinese Restaurant  Clothing Store  \
0                     0       0                   0               0   
1                     0       0                   0               0   
2                     0       0                   0               0   
3                     0       0                   0               0   
4                     0       0                   0               0   

   Cocktail Bar  Coffee Shop  College Basketball Court  Concert Hall  \
0             0            0                         0             1   
1             0            0                         0             0   
2             0            0                         0             0   
3             0            0                         0             0   
4             0            0                         0             0   

   Convenience Store  Cosmetics Shop  Cycle Studio  Dance Studio  \
0                  0               0             0             0   
1                  0               0             0             0   
2                  0               0             0             0   
3                  0               0             0             0   
4                  0               0             0             0   

   Deli / Bodega  Department Store  Dessert Shop  Diner  Discount Store  \
0              0                 0             0      0             

In [56]:
num_top_venues = 5

for hood in final_group['Neighborhood']:
    print("----"+hood+"----")
    temp = final_group[final_group['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond, Toronto----
                     venue  freq
0             Concert Hall   1.0
1                 Pharmacy   0.0
2  New American Restaurant   0.0
3              Opera House   0.0
4        Outdoor Sculpture   0.0


----Agincourt North,L'Amoreaux East,Milliken,Steeles East, Toronto----
                     venue  freq
0                     Park   1.0
1       African Restaurant   0.0
2      Peruvian Restaurant   0.0
3               Nail Salon   0.0
4  New American Restaurant   0.0


----Agincourt, Toronto----
                     venue  freq
0           Breakfast Spot   1.0
1       African Restaurant   0.0
2      Peruvian Restaurant   0.0
3  New American Restaurant   0.0
4              Opera House   0.0


----Albion Gardens,Beaumond Heights,Humbergate,Jamestown,Mount Olive,Silverstone,South Steeles,Thistletown, Toronto----
                     venue  freq
0           Sandwich Place   1.0
1       African Restaurant   0.0
2      Peruvian Restaurant   0.0
3         

In [57]:
# Create the new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = final_group['Neighborhood']

for ind in np.arange(final_group.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(final_group.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.tail()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
395        Woodlawn, New York           Pizza Place           Yoga Studio   
396         Woodrow, New York      Sushi Restaurant           Yoga Studio   
397        Woodside, New York       Thai Restaurant           Yoga Studio   
398  York Mills West, Toronto                  Bank           Yoga Studio   
399       Yorkville, New York             Wine Shop           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
395          Dessert Shop                  Farm   Dumpling Restaurant   
396                  Food  Fast Food Restaurant                  Farm   
397                  Food  Fast Food Restaurant                  Farm   
398     Food & Drink Shop                 Field  Fast Food Restaurant   
399                 Diner  Fast Food Restaurant                  Farm   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
395            Donut Shop               Dog Run        Discount Store   
396   Dumpling Restaurant            Donut Shop               Dog Run   
397   Dumpling Restaurant            Donut Shop               Dog Run   
398                  Farm   Dumpling Restaurant            Donut Shop   
399   Dumpling Restaurant            Donut Shop               Dog Run   

    9th Most Common Venue 10th Most Common Venue  
395                 Diner       Department Store  
396        Discount Store                  Diner  
397        Discount Store                  Diner  
398               Dog Run         Discount Store  
399        Discount Store           Dessert Shop

# Format the two dataframes to run our Cluster Test

array([1, 0, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [58]:
#Evaluate the list of column heads to isolate the neighborhood, lat, and long
toronto_neighbor.head()

Neighborhood  Neighborhood Latitude  \
0                          Rouge,Malvern, Toronto              43.806686   
2   Highland Creek,Rouge Hill,Port Union, Toronto              43.784535   
4        Guildwood,Morningside,West Hill, Toronto              43.763573   
12                                Woburn, Toronto              43.770992   
15                             Cedarbrae, Toronto              43.773136   

    Neighborhood Longitude                            Venue  Venue Latitude  \
0               -79.194353                          Wendy's       43.807448   
2               -79.160497            Royal Canadian Legion       43.782533   
4               -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   
12              -79.216917                        Starbucks       43.770037   
15              -79.239476         Drupati's Roti & Doubles       43.775222   

    Venue Longitude        Venue Category  
0        -79.199056  Fast Food Restaurant  
2        -79.163085                   Bar  
4        -79.189914           Pizza Place  
12       -79.221156           Coffee Shop  
15       -79.241678  Caribbean Restaurant

In [59]:
toronto_edit = toronto_neighbor.filter(['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude'], axis=1)
toronto_edit.head()

Neighborhood  Neighborhood Latitude  \
0                          Rouge,Malvern, Toronto              43.806686   
2   Highland Creek,Rouge Hill,Port Union, Toronto              43.784535   
4        Guildwood,Morningside,West Hill, Toronto              43.763573   
12                                Woburn, Toronto              43.770992   
15                             Cedarbrae, Toronto              43.773136   

    Neighborhood Longitude  
0               -79.194353  
2               -79.160497  
4               -79.188711  
12              -79.216917  
15              -79.239476

In [60]:
#We'll need to drop borough 
newyork_edit = ny_neighborhoods.filter(['Neighborhood', 'Latitude', 'Longitude'], axis=1)
newyork_edit.head()

Neighborhood   Latitude  Longitude
0    Wakefield, New York  40.894705 -73.847201
1   Co-op City, New York  40.874294 -73.829939
2  Eastchester, New York  40.887556 -73.827806
3    Fieldston, New York  40.895437 -73.905643
4    Riverdale, New York  40.890834 -73.912585

In [61]:
#Rename the column heads to match each other
toronto_edit.rename(columns={'Neighborhood Latitude':'Latitude',
                            'Neighborhood Longitude':'Longitude'},
                    inplace=True)
toronto_edit.head()

Neighborhood   Latitude  Longitude
0                          Rouge,Malvern, Toronto  43.806686 -79.194353
2   Highland Creek,Rouge Hill,Port Union, Toronto  43.784535 -79.160497
4        Guildwood,Morningside,West Hill, Toronto  43.763573 -79.188711
12                                Woburn, Toronto  43.770992 -79.216917
15                             Cedarbrae, Toronto  43.773136 -79.239476

In [62]:
#Combine toronto_edit and newyork_edit

frames = [toronto_edit, newyork_edit]
neighborhood_df = pd.concat(frames)
neighborhood_df.head()

Neighborhood   Latitude  Longitude
0                          Rouge,Malvern, Toronto  43.806686 -79.194353
2   Highland Creek,Rouge Hill,Port Union, Toronto  43.784535 -79.160497
4        Guildwood,Morningside,West Hill, Toronto  43.763573 -79.188711
12                                Woburn, Toronto  43.770992 -79.216917
15                             Cedarbrae, Toronto  43.773136 -79.239476

# Determining K cluster value

In [79]:
# Use Kmeans clustering to determine the cluster number 5

In [114]:
# Set the number of clusters
kclusters = 3

final_clustering = final_group.drop('Neighborhood', 1)

# Run the k-means clustering.
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(final_clustering)

# Check the cluster labels generated for each row in the dataframe.
kmeans.labels_[0:10]

array([0, 1, 0, 0, 2, 2, 0, 2, 0, 2], dtype=int32)

In [115]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

neighborhood_merged = neighborhood_df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
neighborhood_merged = neighborhood_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

In [116]:
neighborhood_merged.head()

Neighborhood   Latitude  Longitude  \
0                          Rouge,Malvern, Toronto  43.806686 -79.194353   
2   Highland Creek,Rouge Hill,Port Union, Toronto  43.784535 -79.160497   
4        Guildwood,Morningside,West Hill, Toronto  43.763573 -79.188711   
12                                Woburn, Toronto  43.770992 -79.216917   
15                             Cedarbrae, Toronto  43.773136 -79.239476   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0              0.0  Fast Food Restaurant           Yoga Studio   
2              0.0                   Bar           Yoga Studio   
4              2.0           Pizza Place           Yoga Studio   
12             0.0           Coffee Shop                 Diner   
15             0.0  Caribbean Restaurant           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Diner                  Farm   Dumpling Restaurant   
2      Food & Drink Shop                 Field  Fast Food Restaurant   
4           Dessert Shop                  Farm   Dumpling Restaurant   
12  Fast Food Restaurant                  Farm   Dumpling Restaurant   
15                 Diner  Fast Food Restaurant                  Farm   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0             Donut Shop               Dog Run        Discount Store   
2                   Farm   Dumpling Restaurant            Donut Shop   
4             Donut Shop               Dog Run        Discount Store   
12            Donut Shop               Dog Run        Discount Store   
15   Dumpling Restaurant            Donut Shop               Dog Run   

   9th Most Common Venue 10th Most Common Venue  
0           Dessert Shop                   Food  
2                Dog Run         Discount Store  
4                  Diner       Department Store  
12          Dessert Shop                   Food  
15        Discount Store           Dessert Shop

In [117]:
neighborhood_merged=neighborhood_merged.dropna(axis=0, how='any', thresh=None, subset=None, inplace=False)

In [118]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = [-1,0,1,2]
for lat, lon, poi, cluster in zip(neighborhood_merged['Latitude'], neighborhood_merged['Longitude'], neighborhood_merged['Neighborhood'], neighborhood_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-0],
        fill=True,
        fill_color=rainbow[int(cluster)-0],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Evaluate the Clusters 

In [119]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 0, neighborhood_merged.columns[[0] + list(range(5, neighborhood_merged.shape[1]))]]

Neighborhood 2nd Most Common Venue  \
0                                Rouge,Malvern, Toronto           Yoga Studio   
2         Highland Creek,Rouge Hill,Port Union, Toronto           Yoga Studio   
12                                      Woburn, Toronto                 Diner   
15                                   Cedarbrae, Toronto           Yoga Studio   
24                         Scarborough Village, Toronto           Yoga Studio   
26    East Birchmount Park,Ionview,Kennedy Park, Tor...           Yoga Studio   
31               Clairlea,Golden Mile,Oakridge, Toronto                 Diner   
41    Cliffcrest,Cliffside,Scarborough Village West,...           Yoga Studio   
44                  Birch Cliff,Cliffside West, Toronto                 Diner   
48    Dorset Park,Scarborough Town Centre,Wexford He...                 Diner   
54                            Maryvale,Wexford, Toronto           Yoga Studio   
62                                   Agincourt, Toronto           Yoga Studio   
66       Clarks Corners,Sullivan,Tam O'Shanter, Toronto           Yoga Studio   
82                             L'Amoreaux West, Toronto           Yoga Studio   
96                           Hillcrest Village, Toronto           Yoga Studio   
101                 Fairview,Henry Farm,Oriole, Toronto                  Food   
168                            Bayview Village, Toronto           Yoga Studio   
172                    Silver Hills,York Mills, Toronto           Yoga Studio   
174                           Willowdale South, Toronto           Yoga Studio   
209                            York Mills West, Toronto           Yoga Studio   
221                            Don Mills North, Toronto           Yoga Studio   
227            Flemingdon Park,Don Mills South, Toronto           Yoga Studio   
248   Bathurst Manor,Downsview North,Wilson Heights,...           Yoga Studio   
267             Northwood Park,York University, Toronto           Yoga Studio   
273                 CFB Toronto,Downsview East, Toronto           Yoga Studio   
276                             Downsview West, Toronto           Yoga Studio   
281                          Downsview Central, Toronto           Yoga Studio   
283                        Downsview Northwest, Toronto           Yoga Studio   
287                           Victoria Village, Toronto           Yoga Studio   
291             Woodbine Gardens,Parkview Hill, Toronto           Yoga Studio   
303                           Woodbine Heights, Toronto           Yoga Studio   
313                                The Beaches, Toronto           Yoga Studio   
320                                    Leaside, Toronto           Yoga Studio   
354                           Thorncliffe Park, Toronto           Yoga Studio   
377                The Danforth West,Riverdale, Toronto           Yoga Studio   
418              The Beaches West,India Bazaar, Toronto           Yoga Studio   
437                            Studio District, Toronto                 Diner   
490                         North Toronto West, Toronto                 Diner   
510                                 Davisville, Toronto                 Diner   
548                 Moore Park,Summerhill East, Toronto           Yoga Studio   
550   Deer Park,Forest Hill SE,Rathnelly,South Hill,...           Yoga Studio   
565                                   Rosedale, Toronto           Yoga Studio   
569                 Cabbagetown,St. James Town, Toronto                 Diner   
614                       Church and Wellesley, Toronto           Yoga Studio   
695                               Harbourfront, Toronto           Yoga Studio   
742                    Ryerson,Garden District, Toronto           Yoga Studio   
842                             St. James Town, Toronto           Yoga Studio   
942                                Berczy Park, Toronto                 Diner   
998                         Central Bay Street, Toronto                 Di

In [120]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 1, neighborhood_merged.columns[[0] + list(range(5, neighborhood_merged.shape[1]))]]

Neighborhood 2nd Most Common Venue  \
80    Agincourt North,L'Amoreaux East,Milliken,Steel...           Yoga Studio   
218                                  Parkwoods, Toronto           Yoga Studio   
373                               East Toronto, Toronto           Yoga Studio   
479                              Lawrence Park, Toronto           Yoga Studio   
482                           Davisville North, Toronto           Yoga Studio   
1885                       Caledonia-Fairbanks, Toronto           Yoga Studio   
2090                              Queen's Park, Toronto           Yoga Studio   
2180  The Kingsway,Montgomery Road,Old Mill North, T...           Yoga Studio   
13                               Bedford Park, New York           Yoga Studio   
27                               Clason Point, New York           Yoga Studio   
35                             Spuyten Duyvil, New York           Yoga Studio   
79                                 Bath Beach, New York           Yoga Studio   
114                                   Midtown, New York           Yoga Studio   
120                                   Tribeca, New York           Yoga Studio   
127                         Battery Park City, New York           Yoga Studio   
155                                 Glen Oaks, New York           Yoga Studio   
167                       Springfield Gardens, New York           Yoga Studio   
192                                Somerville, New York           Yoga Studio   
203                                 Todt Hill, New York           Yoga Studio   
274                                Tudor City, New York           Yoga Studio   
279                              Fulton Ferry, New York           Yoga Studio   
295                             Highland Park, New York           Yoga Studio   
301                              Hudson Yards, New York           Yoga Studio   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
80                    Farm   Dumpling Restaurant            Donut Shop   
218                   Farm   Dumpling Restaurant            Donut Shop   
373                   Farm   Dumpling Restaurant            Donut Shop   
479                   Farm   Dumpling Restaurant            Donut Shop   
482                   Farm   Dumpling Restaurant            Donut Shop   
1885                  Farm   Dumpling Restaurant            Donut Shop   
2090                  Farm   Dumpling Restaurant            Donut Shop   
2180                  Farm   Dumpling Restaurant            Donut Shop   
13                    Farm   Dumpling Restaurant            Donut Shop   
27                    Farm   Dumpling Restaurant            Donut Shop   
35                    Farm   Dumpling Restaurant            Donut Shop   
79                    Farm   Dumpling Restaurant            Donut Shop   
114                   Farm   Dumpling Restaurant            Donut Shop   
120                   Farm   Dumpling Restaurant            Donut Shop   
127                   Farm   Dumpling Restaurant            Donut Shop   
155                   Farm   Dumpling Restaurant            Donut Shop   
167                   Farm   Dumpling Restaurant            Donut Shop   
192                   Farm   Dumpling Restaurant            Donut Shop   
203                   Farm   Dumpling Restaurant            Donut Shop   
274                   Farm   Dumpling Restaurant            Donut Shop   
279                   Farm   Dumpling Restaurant            Donut Shop   
295                   Farm   Dumpling Restaurant            Donut Shop   
301                   Farm   Dumpling Restaurant            Donut Shop   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
80                 Dog Run        Discount Store                 Diner   
218                Dog Run        Discount Store                 Diner   
373                Dog Run        Discount Store                 Diner   
479                Dog Ru

In [121]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 2, neighborhood_merged.columns[[0] + list(range(5, neighborhood_merged.shape[1]))]]

Neighborhood 2nd Most Common Venue  \
4     Guildwood,Morningside,West Hill, Toronto           Yoga Studio   
212                   Willowdale West, Toronto           Yoga Studio   
2011     The Junction North,Runnymede, Toronto           Yoga Studio   
2171            Alderwood,Long Branch, Toronto           Yoga Studio   
2206                    Humber Summit, Toronto           Yoga Studio   
6                        Marble Hill, New York           Yoga Studio   
7                           Woodlawn, New York           Yoga Studio   
8                            Norwood, New York           Yoga Studio   
25                        Morrisania, New York           Yoga Studio   
32                          Van Nest, New York           Yoga Studio   
36                   North Riverdale, New York           Yoga Studio   
71                     Cypress Hills, New York           Yoga Studio   
92                           Midwood, New York           Yoga Studio   
97                        South Side, New York           Yoga Studio   
137                    Richmond Hill, New York           Yoga Studio   
142                          Maspeth, New York           Yoga Studio   
147                       Ozone Park, New York           Yoga Studio   
157                Kew Gardens Hills, New York           Yoga Studio   
161                  Oakland Gardens, New York           Yoga Studio   
170                     Far Rockaway, New York           Yoga Studio   
181                      Floral Park, New York           Yoga Studio   
197                       St. George, New York           Yoga Studio   
208                Castleton Corners, New York           Yoga Studio   
214                      Eltingville, New York           Yoga Studio   
228                         Arrochar, New York           Yoga Studio   
231                     Dongan Hills, New York           Yoga Studio   
241                    Arden Heights, New York           Yoga Studio   
258                         Elm Park, New York           Yoga Studio   
291                     Prince's Bay, New York           Yoga Studio   
297                        Bronxdale, New York           Yoga Studio   
298                         Allerton, New York           Yoga Studio   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
4             Dessert Shop                  Farm   Dumpling Restaurant   
212           Dessert Shop                  Farm   Dumpling Restaurant   
2011          Dessert Shop                  Farm   Dumpling Restaurant   
2171          Dessert Shop                  Farm   Dumpling Restaurant   
2206          Dessert Shop                  Farm   Dumpling Restaurant   
6             Dessert Shop                  Farm   Dumpling Restaurant   
7             Dessert Shop                  Farm   Dumpling Restaurant   
8             Dessert Shop                  Farm   Dumpling Restaurant   
25            Dessert Shop                  Farm   Dumpling Restaurant   
32            Dessert Shop                  Farm   Dumpling Restaurant   
36            Dessert Shop                  Farm   Dumpling Restaurant   
71            Dessert Shop                  Farm   Dumpling Restaurant   
92            Dessert Shop                  Farm   Dumpling Restaurant   
97            Dessert Shop                  Farm   Dumpling Restaurant   
137           Dessert Shop                  Farm   Dumpling Restaurant   
142           Dessert Shop                  Farm   Dumpling Restaurant   
147           Dessert Shop                  Farm   Dumpling Restaurant   
157           Dessert Shop                  Farm   Dumpling Restaurant   
161           Dessert Shop                  Farm   Dumpling Restaurant   
170           Dessert Shop                  Farm   Dumpling Restaurant   
181           Dessert Shop                  Farm   Dumpling Restaurant   
197           Dessert Shop                  Farm   Dumpling Restaurant   
208           Dessert Shop 

# Conclusion

### You can use the above cluster information to find comparable neighborhoods within New York Ciy and Toronto based on nearby venues.